# 時間枠付き巡回セールスマン問題(Traveling Salesman Problem with Time Windows; TSPTW)

> このチュートリアルは現在改訂中のため、動作しない可能性があります。

## 概要

TSPでは巡回する最短距離を求めていました。TSPTWでは点$i$と点$j$地点間の移動距離$c_{ij}$を移動時間とみなし、さらに点$i$の出発時刻$t_i$が最早時刻$e_i$と最遅時刻$\ell_i$の間でなければならないという制約を課します。ただし時刻$e_i$より早く点$i$に到着した場合には、点$i$上で時刻$e_i$まで待つことができます。このような制約の中で、移動時間を最小にするような経路を求めるのがTSPTWです。

この問題はTSPと同様にNP困難ですが、実行可能解が存在するかどうかを判定する問題ではNP完全となります。

![時間枠付き巡回セールスマン問題](./images/tsptw_01.png)

## 応用例: 時間枠付き配送計画問題(Vehicle Routing Problem with Time Window; VRPTW)

TSPの章で述べたとおり、VRPはTSPをより一般化したものです。このVRPにさらに時間枠をつけたものがVRPTWです。具体的には指定された時間(例えば午後1時から午後3時の間)にある顧客にトラックで荷物を届ける、というような具合です。このような制約を満たしつつ複数の顧客を回り、荷物を届ける際の配送コストを最小にするようなルートを発見するのがVRPTWです。

今回は様々な応用が効きそうなTSPTWを題材に、JijModelingとJijZeptの使い方をご紹介いたします。 

# 数理モデル立案

## バイナリ変数

$x_{ij}$を地点$i$の次に地点$j$を訪問するとき1、そうでないとき0となるようなバイナリ変数とします。またこの問題では出発する時刻も考える必要があるため、地点$i$を出発する時刻を表す変数として$t_i$を導入します。$t_i = \sum_k 2^k t_{i, k} \ (t_{i, k} \in \{ 0, 1\})$は正の整数しか取り得ないとして、この問題を整数計画問題として扱います。

## 制約1: 地点$i$から地点$j$に向かう枝は1本でなければならない

地点$i$から出発したセールスマンが向かう先は一つでなければなりません(セールスマンは1人しか考えていないため、分身して同時に別々の点に向かうことは許されません)。これを数式として表現すると

$$\sum_{j \neq i} x_{ij} = 1 \quad (\forall i) \tag{1}$$

## 制約2: 地点$i$に入る枝は1本でなけらばならない

地点$i$に到達する道は地点$i$とその他の点を結ぶ道路の数だけ存在しますが、そのうちの1本だけを通って地点$i$にセールスマンがやってくる必要があります(セールスマンは1人しか考えていないため、2人以上のセールスマンが別々の地点から地点$i$に集合することは許されません)。これを数式として表現すると

$$\sum_{j \neq i} x_{ji} = 1 \quad (\forall i) \tag{2}$$

## 制約3: 出発時刻は許される時間の範囲内でなければならない

時間枠付きTSPはその名の通り、出発時刻に許されている時間枠が存在します。

$$e_i \leq t_i \leq \ell_i \quad (\forall i : i\neq 1) \tag{3}$$

ただしセールスマンが最初に出発する時刻の制限は考えません( $e_1 = 0, \ell_1= \infty$)。

## 制約4: 地点$i$の次の地点$j$を出発する時刻は、地点$i$の出発時刻と地点$i$から地点$j$の移動時間の和より大きくなければならない

地点$i$から地点$j$に移動するのにかかる時間が$c_{ij}$なので、地点$j$からの出発時刻$t_j$は以下の不等式を満たさなければなりません。

$$t_i + c_{ij} \leq t_j \quad (\forall i, j: i \neq 0, j\neq 0, i\neq j) \tag{4}$$

## 目的関数

最小化したいのは移動時間の合計なので

$$\mathrm{obj}= \sum_i \sum_{j\neq i} c_{ij} x_{ij} \tag{5}$$

です。

# 実装しましょう

それではJijのプロダクトを用いて、この問題を解くためのPythonスクリプトを作成しましょう。

## JijModelingで問題の作成

### 初期化

In [1]:
import jijmodeling as jm

# set problem
problem = jm.Problem('TSPTW')

### 変数の定義

In [2]:
# define variables
c = jm.Placeholder('c', dim=2)
N = c.shape[0]
e = jm.Placeholder('e', shape=(N))
l = jm.Placeholder('l', shape=(N))
x = jm.Binary('x', shape=(N, N))
t = jm.LogEncIntArray('t', shape=(N), lower=e, upper=l)
i = jm.Element('i', (0, N))
j = jm.Element('j', (0, N))

`c`は各地点間の移動時間を表す2次元リスト、`N`は訪れる地点の総数、`e`と`l`はそれぞれ各地点を出発する最早時間・最遅時間を格納した1次元リストです。  
`x`は$\{0, 1\}$のバイナリ変数列です。  
`t`は$e_i \leq t_i \leq \ell_i$を満たす2進数表現の整数変数列で、これを`LogEncIntArray`で定義しています。考える地点によって$t_i$の下限と上限が異なるため、`lower`と`upper`を`t`と同じ形(`shape=(N)`)を持つ変数列`e`, `l`によって表現しています。  
最後に、これから制約および目的関数の実装で用いる添字`i`, `j`を`Element`で定義しています。

### 制約の実装

(1)式を実装しましょう。

In [3]:
# set one-hot constraint for outward
const = jm.Sum((j, j!=i), x[i, j])
# const = jm.Sum(j, x[i, j])
problem += jm.Constraint('h1', const==1, forall=i)

(1)式の$\sum_{j \neq i} x_{ij}$を`jm.Sum((j, j!=i), x[i, j])`で表現しています。`Sum((添字, 添字の条件), 総和をとる数式)`のようにして条件を指定できます。  
$j \neq i$を`j!=i`で表現しています。他にも`j>i`, `j>=i`, `j<i`, `j<=i`などを使うことができます。  
次に(2)式です。

In [13]:
# set one-hot constraint for inward
const = jm.Sum((j, j!=i), x[j, i])
problem += jm.Constraint('h2', const==1, forall=i)

先程の(1)式の実装テクニックと同じものを用いています。  
(3)式は変数定義部分において`e<t<l`のようにして時間を表す変数`t`の取りうる範囲を決めているため、自明に成り立ちます。最後に(4)式です。

In [17]:
## set time window constraint
const = t[i] + c[i, j] - t[j]
forall_list = [(j, j!=0), (i, (i!=0)&(i!=j))]
problem += jm.Constraint('h3', const<=0, forall=forall_list)

(4)式では$\forall i, \forall j$について考える必要があります。複数の添字について`forall`を指定するに上述のスクリプトのように、添字に関する情報をリストにまとめます。このとき添字$i$については$i \neq j$と$i \neq 0$、そして添字$j$については$j \neq 0$でなければならないため、これらの条件を指定する必要があります。それには`(添字: 添字に対する条件)`のようにすることで、その添字に対して条件を課すことができます。

> (注意): この場合、[(i, (i!=0)&(i!=j)), (j, j!=0)]のように実装することはできません。このように実装すると`i!=j`の部分で`j`が定義されていないと判断され、エラーが返されます。複数の添字に対して`forall`を指定する場合には、その添字に課される条件から、実装する順序に気をつけましょう。

またここでは、添字$i$について$i \neq 0$と$i \neq j$の2つの条件が課されています。このような場合、AND演算子`&`を用いて複数条件を同時に満たすような`i`を設定することが可能です。同様にどちらかの条件を課したい場合、OR演算子の`|`を用いることもできます。

### 目的関数の実装

制約の次は(5)式の目的関数です。

In [27]:
# set objective function
sum_list = [i, (j, j!=i)]
obj = jm.Sum(sum_list, c[i, j]*x[i, j])
problem += obj

$\sum_i \sum_{j\neq i}$という条件がある2つの総和を1つの`jm.Sum`で表現するために、先程のテクニックを用いて`jm.Sum(添字の範囲を指定したリスト, 総和を取る数式)`のようにしています。添字の範囲を指定している部分において、`(添字, 添字が満たす条件)`のようにすることで、条件を満たす部分のみの総和を考えることができます。

> (注意): ここでも[(j, j!=i), i]のようにすると、`j!=i`の部分で`i`が定義されていないと判断され、エラーが返ってきます。これは$\sum_i \sum_{j\neq i}$のように、数式の総和記号の順序からの類推と見ることもできます。

ここまでで作成してきた問題の実装を見てみましょう。

In [4]:
problem

## インスタンスの作成

実際に2つの地点間の移動時間と各地点の最早・最遅時間を与えてみましょう。

In [5]:
import numpy as np

# set the number of cities
N = 5
# set the matrix of travel time
inst_c = np.random.randint(low=1, high=4, size=(N, N))
inst_c = np.tril(inst_c) + np.tril(inst_c).T - 2 * np.diag(inst_c.diagonal())
# set the list of the ealiest departure time
inst_e = [0, 2, 4, 6, 8]
# set the list of the latest departure time
inst_l = [100, 6, 8, 10, 12]
instance_data = {'c': inst_c, 'e': inst_e, 'l': inst_l}

## 未定乗数の決定

(10)式の$\lambda_1, \lambda_2, \lambda_3$を設定しましょう。ここでは3つとも10としています。

In [6]:
# set multipliers
lam1 = 10.0
lam2 = 10.0
lam3 = 10.0
multipliers = {'h1': lam1, 'h2': lam2, 'h3': lam3}

## JijZeptで解く

`JijZept`のSAを用いて問題を解きます。

In [7]:
import jijzept as jz

# set sampler
sampler = jz.JijSASampler(config='./config.toml')
# solve problem
response = sampler.sample_model(problem, instance_data, multipliers, 
                                num_reads=200, num_sweeps=100)

uploading instance ...
submitting query ...
submitted to the queue.
Your solution_id is 8dee7c57038c442f9462eadb0b6277bf.


## 解析しやすくする

出てきた結果を解析しやすくするために、decodeを行いましょう。

In [8]:
# decode solution
decoded = problem.decode(response, instance_data, {})

DataError: You need variable_list.

## 結果の可視化

decodeされた結果を見てみましょう。

In [49]:
x = decoded[0]['solution']['x']
print(x)


[[0. 0. 0. 0. 1.]
 [0. 1. 0. 0. 0.]
 [0. 0. 1. 0. 0.]
 [0. 0. 0. 0. 1.]
 [0. 0. 1. 0. 0.]]


0→1→2→3→4→0という順番に巡回していることがわかります。`penalty`の`h3`の値が0になっていませんが、実際に出発時刻を見ると全ての地点で最早時間と最遅時間の間に出発できています。これは例えば(9)式において$t_j = 5, t_i + c_{ij} - (\ell_i + c_{ij} - e_j) (1-x_{ij})=1, Y_{ij}=0$の場合、(4)式は満たされていますが、(9)式の計算からは$H_3 \neq 0$となってしまうためです。不等式制約の場合には「制約が正しく満たされているか」を数理モデルの数式までさかのぼって確認する必要があります。

# 結言

今回は時間枠付き巡回セールスマン問題から、JijModelingとJijZeptの使い方をご紹介しました。今回登場したテクニックを以下にまとめます。

- 不等式制約などで用いるスラック変数が複数ある場合、LogEncIntArrayによってスラック変数列を1度に定義することができる。このときlowerとupperに同じshapeの変数を指定することで、個別に範囲を割り当てることができる。
- 総和計算ではjm.Sum({添字: 添字の範囲}, 総和をとる数式, 条件)のようにすることで、和を取るときの条件を設定することができる。
- $\sum_{i} \sum_{j\neq i} \sum_{k>i}$のような場合、条件についても[None, jm.neq(j, i), k>i]のように1つのリストにまとめることで、jm.Sumを1つ書くだけで表現できる。
- 複数条件ある場合、例えば$\sum_{i \neq 10, i > 5} x_i$のような場合にはjm.Sum({i: N}, x[i], jm.neq(i, 10)&(i>5))のように論理演算子を用いて条件を連ねることができる。

これらのテクニックを用いることで、複雑な数式を容易に実装することが可能です。

# 参考文献

[1] [Savelsbergh, 1985, "Local search in routing problems with time windows"](https://doi.org/10.1007/BF02022044)  
[2] [Kara, Derya, 2015, "Formulation for Minimizing Tour Duration of the Traveling Salesman Problem with Time Windows"](https://www.sciencedirect.com/science/article/pii/S2212567115009260?via%3Dihub)  
[3] [Lucas, 2013, "Ising formulation of many NP problems"](https://www.frontiersin.org/articles/10.3389/fphy.2014.00005/full)